## Initialization

In [ ]:
import duckdb
import pandas as pd
import glob

%config SqlMagic.autopandas = True
%config SqlMagic.feedback = False
%config SqlMagic.displaylimit = 10

pd.set_option("display.precision", 2)

con = duckdb.connect()

%reload_ext sql
%sql con --alias duckdb

## Loading

Load railway services in the Netherlands

* Start date: January 2019
* End date: April 2024

Total: **15 GB of CSV files**

In [ ]:
%%sql
CREATE TABLE services AS FROM 'services-*.csv.gz';
SELECT format('{:,}', count(*)) AS num_services FROM services;

In [ ]:
%%sql
SELECT
    year("Service:Date") AS year,
    avg("Stop:Arrival delay") * 60 AS delay
FROM services
GROUP BY ALL;

In [ ]:
%%sql --save delays
SELECT
    year("Service:Date") AS year,
    avg("Stop:Arrival delay") * 60 AS delay
FROM services
GROUP BY ALL;

In [ ]:
%%sql
delays_df << SELECT * FROM delays;

In [ ]:
delays_df.plot.bar(
        x = "year", \
        y = "delay", \
        figsize = (5, 3)
    )

## Pandas

* Loading: 106 seconds
* Aggregation: 6 seconds
* **Total: 112 seconds**

In [ ]:
df = pd.concat(map(pd.read_csv, glob.glob("*.csv")))
df["year"] = pd.to_datetime(df["Service:Date"]).dt.year
df.groupby("year")["Stop:Arrival delay"].mean()

## Queries

In [ ]:
%%sql
SELECT
    "Stop:station name" AS station,
    format('{:,}', count(*)) AS num_services
FROM services
GROUP BY ALL
ORDER BY num_services DESC
LIMIT 5;

In [ ]:
%%sql
CREATE TABLE services_per_month AS
    SELECT
        month("Service:Date") AS month,
        "Stop:station name" AS station,
        count(*) AS num_services
    FROM services
    GROUP BY ALL;

In [ ]:
%%sql
SELECT month, month_name, array_agg(station) AS top_stations
FROM (
    SELECT
        month,
        strftime(make_date(2023, month, 1), '%B') AS month_name,
        rank() OVER
            (PARTITION BY month ORDER BY num_services DESC) AS rank,
        station,
        num_services
    FROM services_per_month
)
WHERE rank <= 3
GROUP BY ALL
ORDER BY month;

## Pivoting tables

In [ ]:
%%sql
CREATE OR REPLACE TABLE top_stations_per_month AS
    FROM services_per_month
    WHERE station IN ('Utrecht Centraal', 'Amsterdam Centraal', 'Amsterdam Sloterdijk', 'Schiphol Airport');

In [ ]:
%%sql
PIVOT top_stations_per_month
ON station
USING sum(num_services);


### FILTER clause in aggregations

Using the [`FILTER` clause](https://duckdb.org/docs/sql/query_syntax/filter):

In [ ]:
%%sql
SELECT
    datepart('year', "Service:Date") AS year,
    count(*) FILTER ("Service:Completely cancelled" = true) AS cancelled,
    count(*) FILTER ("Service:Completely cancelled" = false) AS not_cancelled,
    printf('%.2f', 100 * cancelled / (cancelled + not_cancelled)) AS percentage
FROM services
GROUP BY ALL
ORDER BY year;


### Unpivoting tables

Turning long tables to wide tables.

In [ ]:
%%sql
CREATE OR REPLACE TABLE stations AS
    FROM 'stations-2022-01.csv';

CREATE OR REPLACE TABLE tariffs AS
    FROM read_csv('tariff-distances-2022-01.csv', header = true, nullstr = 'XXX');

FROM tariffs;

In [ ]:
%%sql
CREATE OR REPLACE TABLE tariffs AS
    UNPIVOT tariffs
    ON COLUMNS (* EXCLUDE Station)
    INTO
        NAME OtherStation
        VALUE Distance;

In [ ]:
%%sql
FROM tariffs
LIMIT 5;

### Joining tables

In [ ]:
%%sql
SELECT s1.name_short, s2.name_short, tariffs.Distance
    FROM tariffs
    JOIN stations s1 ON tariffs.Station = s1.code
    JOIN stations s2 ON tariffs.OtherStation = s2.code
    WHERE Station < OtherStation
      AND s1.country = 'NL'
      AND s2.country = 'NL'
    ORDER BY Distance DESC
    LIMIT 3;